<a href="https://colab.research.google.com/github/maverick98/CDS/blob/main/Code_for_Actor_Critic_Problem.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Group ID:
### Group Members Name with Student ID:
Student 1 Girija Shankar Sahoo 2023AA05235

Student 2 Sourajeet Sahoo 2023aa05029

Student 3 S Sridhar 2023ab05096

Student 4 Manoranjan Sahu 2023aa05738



# Problem Statement

The objective of the problem is to implement an Actor-Critic reinforcement learning algorithm to optimize energy consumption in a building. The agent should learn to adjust the temperature settings dynamically to minimize energy usage while maintaining comfortable indoor conditions.

#### Dataset Details
Dataset: https://archive.ics.uci.edu/dataset/374/appliances+energy+prediction

This dataset contains energy consumption data for a residential building, along with various environmental and operational factors.

Data Dictionary:
* Appliances:       Energy use in Wh
* lights:           Energy use of light fixtures in the house in Wh
* T1 - T9:          Temperatures in various rooms and outside
* RH_1 to RH_9:     Humidity measurements in various rooms and outside
* Visibility:       Visibility in km
* Tdewpoint:       Dew point temperature
* Pressure_mm_hgg:  Pressure in mm Hg
* Windspeed:        Wind speed in m/s

#### Environment Details
**State Space:**
The state space consists of various features from the dataset that impact energy consumption and comfort levels.

* Current Temperature (T1 to T9): Temperatures in various rooms and outside.
* Current Humidity (RH_1 to RH_9): Humidity measurements in different locations.
* Visibility (Visibility): Visibility in meters.
* Dew Point (Tdewpoint): Dew point temperature.
* Pressure (Press_mm_hg): Atmospheric pressure in mm Hg.
* Windspeed (Windspeed): Wind speed in m/s.

Total State Vector Dimension: Number of features = 9 (temperature) + 9 (humidity) + 1 (visibility) + 1 (dew point) + 1 (pressure) + 1 (windspeed) = 22 features

**Target Variable:** Appliances (energy consumption in Wh).

**Action Space:**
The action space consists of discrete temperature adjustments:
* Action 0: Decrease temperature by 1°C
* Action 1: Maintain current temperature
* Action 2: Increase temperature by 1°C


- If the action is to decrease the temperature by 1°C, you'll adjust each temperature feature (T1 to T9) down by 1°C.
- If the action is to increase the temperature by 1°C, you'll adjust each temperature feature (T1 to T9) up by 1°C.
- Other features remain unchanged.

**Policy (Actor):** A neural network that outputs a probability distribution over possible temperature adjustments.

**Value function (Critic):** A neural network that estimates the expected cumulative reward (energy savings) from a given state.

**Reward function:**
The reward function should reflect the overall comfort and energy efficiency based on all temperature readings. i.e., balance between minimising temperature deviations and minimizing energy consumption.

* Calculate the penalty based on the deviation of each temperature from the target temperature and then aggregate these penalties.
* Measure the change in energy consumption before and after applying the RL action.
* Combine the comfort penalty and energy savings to get the final reward.

*Example:*

Target temperature=22°C

Initial Temperatures: T1=23, T2=22, T3=21, T4=23, T5=22, T6=21, T7=24, T8=22, T9=23

Action Taken: Decrease temperature by 1°C for each room

Resulting Temperatures: T1 = 22, T2 = 21, T3 = 20, T4 = 22, T5 = 21, T6 = 20, T7 = 23, T8 = 21, T9 = 22

Energy Consumption: 50 Wh (before RL adjustment) and 48 Wh (after RL adjustment)
* Energy Before (50 Wh): Use the energy consumption from the dataset at the current time step.
* Energy After (48 Wh): Use the energy consumption from the dataset at the next time step (if available).

Consider only temperature features for deviation calculation.

Deviation = abs (Ti− Ttarget )

Deviations=[ abs(22−22), abs(21−22), abs(20−22), abs(22−22),  abs(21−22), abs(20−22), abs(23−22), abs(21−22), abs(22−22) ]

Deviations = [0, 1, 2, 0, 1, 2, 1, 1, 0], Sum of deviations = 8

Energy Savings = Energy Before−Energy After = 50 – 48 = 2Wh

Reward= −Sum of Deviations + Energy Savings = -8+6 = -2

#### Expected Outcomes
1. Pre-process the dataset to handle any missing values and create training and testing sets.
2. Implement the Actor-Critic algorithm using TensorFlow.
3. Train the model over 500 episodes to minimize energy consumption while maintaining an indoor temperature of 22°C.
4. Plot the total reward obtained in each episode to evaluate the learning progress.
5. Evaluate the performance of the model on test set to measure its performance
6. Provide graphs showing the convergence of the Actor and Critic losses.
7. Plot the learned policy by showing the action probabilities across different state values (e.g., temperature settings).
8. Provide an analysis on a comparison of the energy consumption before and after applying the reinforcement learning algorithm.


In [157]:
!wget https://archive.ics.uci.edu/static/public/374/appliances+energy+prediction.zip
!unzip /content/appliances+energy+prediction.zip

--2024-09-15 08:59:37--  https://archive.ics.uci.edu/static/public/374/appliances+energy+prediction.zip
Resolving archive.ics.uci.edu (archive.ics.uci.edu)... 128.195.10.252
Connecting to archive.ics.uci.edu (archive.ics.uci.edu)|128.195.10.252|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified
Saving to: ‘appliances+energy+prediction.zip’

appliances+energy+p     [      <=>           ]  11.42M  7.37MB/s    in 1.6s    

2024-09-15 08:59:40 (7.37 MB/s) - ‘appliances+energy+prediction.zip’ saved [11979507]

Archive:  /content/appliances+energy+prediction.zip
 extracting: energydata_complete.csv  


# Required Libraries

In [158]:
import pandas as pd
import numpy as np
import tensorflow as tf
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt

#### Code Execution

#1. Pre-process the dataset

In [178]:
 # Define features and target
features = ['T1', 'T2', 'T3', 'T4', 'T5', 'T6', 'T7', 'T8', 'T9', 'RH_1', 'RH_2', 'RH_3', 'RH_4', 'RH_5', 'RH_6', 'RH_7', 'RH_8', 'RH_9', 'Visibility', 'Tdewpoint', 'Press_mm_hg', 'Windspeed']
target = 'Appliances'


In [179]:
def load_and_preprocess_data(file_path):
    data = pd.read_csv(file_path)
    # Convert 'date' column to datetime objects
    data['date'] = pd.to_datetime(data['date'])

    # Handle missing values for numeric features only
    numeric_data = data.select_dtypes(include=[np.number])
    numeric_data.fillna(numeric_data.mean(), inplace=True)
    data[numeric_data.columns] = numeric_data

    # Handle missing values (Example: Fill with mean)
    data.fillna(data.mean(), inplace=True)


    X = data[features]
    y = data[target]

    # Normalize features
    scaler = StandardScaler()
    X_scaled = scaler.fit_transform(X)

    # Split data into training and testing sets
    X_train, X_test, y_train, y_test = train_test_split(X_scaled, y, test_size=0.2, random_state=0)

    return data,X_train, X_test, y_train, y_test

#### Defining Actor Critic Model using tensorflow (1 M)

In [188]:
def build_actor_model(state_dim, action_dim):
    model = tf.keras.Sequential([
        tf.keras.layers.Input(shape=(state_dim,)),
        tf.keras.layers.Dense(24, activation='relu'),
        tf.keras.layers.Dense(24, activation='relu'),
        tf.keras.layers.Dense(action_dim, activation='softmax')
    ])
    model.compile(loss='categorical_crossentropy',optimizer=tf.keras.optimizers.Adam(learning_rate=0.001))
    return model

def build_critic_model(state_dim):
    model = tf.keras.Sequential([
        tf.keras.layers.Input(shape=(state_dim,)),
        tf.keras.layers.Dense(24, activation='relu'),
        tf.keras.layers.Dense(24, activation='relu'),
        tf.keras.layers.Dense(1)
    ])
    model.compile(loss='mse',optimizer=tf.keras.optimizers.Adam(learning_rate=0.001))
    return model

### Reward Function (0.5 M)

In [181]:
def calculate_reward(initial_energy, final_energy, temp_deviations):
    deviation_penalty = -np.sum(temp_deviations)
    energy_savings = initial_energy - final_energy
    reward = deviation_penalty + energy_savings
    return reward

#### Environment Simulation (0.5 M)


In [190]:
def find_matching_index(df, ndarray, features):
    state = pd.Series(ndarray, index=features)
    matching_columns = state.index
    subset_df = df[matching_columns]
    state_df = pd.DataFrame([state], columns=matching_columns)
    current_index = subset_df[subset_df.isin(state_df.to_dict(orient='list')).all(axis=1)].index
    #return current_index.tolist()[0] if not current_index.empty else None
    return current_index
def simulate_environment(action, state, data):
    next_state = state.copy()

    # Adjust temperatures based on action
    if action == 0:  # Decrease temperature
        next_state[:9] -= 1
    elif action == 2:  # Increase temperature
        next_state[:9] += 1
    #print('MS debug 1')
    # Get energy before and after the action
    current_index=find_matching_index(data, state, features)

    next_index = current_index + 1
    if next_index >= len(data):
        next_index = len(data) - 1
    energy_before = data.iloc[current_index]['Appliances']
    energy_after = data.iloc[next_index]['Appliances']

    # Calculate the reward
    temp_deviations = np.abs(next_state[:9] - 22)  # assuming 22°C as target
    reward = calculate_reward(energy_before, energy_after, temp_deviations)

    return next_state, reward

#### Implementation of Training Function (2 M)

In [205]:
def train_actor_critic(X_train, y_train,data_df, episodes=500):
    state_dim = X_train.shape[1]
    action_dim = 3  # Decrease, Maintain, Increase

    actor_model = build_actor_model(state_dim, action_dim)
    critic_model = build_critic_model(state_dim)

    rewards = []

    for episode in range(episodes):
        print(f'episode {episode}')
        state = X_train[np.random.randint(0, len(X_train))]
        done = False

        while not done:
            # Get action probabilities and choose action
            action_probs = actor_model.predict(state.reshape(1, -1))
            action = np.random.choice(action_dim, p=action_probs[0])

            # Simulate environment
            next_state, reward = simulate_environment(action, state, data_df)
            reward = tf.convert_to_tensor(reward, dtype=tf.float32)

            # Update Critic
            target = reward + 0.99 * critic_model.predict(next_state.reshape(1, -1))
            critic_model.train_on_batch(state.reshape(1, -1), target)

            # Calculate advantages
            advantages = reward - critic_model.predict(state.reshape(1, -1))

            # Update Actor
            with tf.GradientTape() as tape:
                action_probs = actor_model(state.reshape(1, -1))
                action_log_probs = tf.math.log(action_probs[0][action])
                loss = -action_log_probs * advantages
            grads = tape.gradient(loss, actor_model.trainable_variables)
            actor_model.optimizer.apply_gradients(zip(grads, actor_model.trainable_variables))

            state = next_state
            done = True  # Simplified for demonstration

        rewards.append(reward.numpy())

    return actor_model, critic_model, rewards

#### Evaluate the performance of the model on test set (0.5 M)

In [213]:
def evaluate_model(actor_model, X_test, y_test,data_df):
    total_rewards = []
    for i in range(len(X_test)):
        print(f'i = {i}')
        state = X_test[i]
        action_probs = actor_model.predict(state.reshape(1, -1))
        action = np.argmax(action_probs)
        print(f'max action {action}')
        next_state, reward = simulate_environment(action, state, data_df)
        print(f'next_state, reward {next_state}, {reward}')
        total_rewards.append(reward)
        print(f'reward {reward}')
    return np.mean(total_rewards)

### Plot the convergence of Actor and Critic losses (1 M)

In [200]:
def plot_results(rewards, actor_loss, critic_loss):
    plt.figure(figsize=(12, 5))
    plt.subplot(1, 3, 1)
    plt.plot(rewards)
    plt.title('Total Reward per Episode')

    plt.subplot(1, 3, 2)
    plt.plot(actor_loss)
    plt.title('Actor Loss')

    plt.subplot(1, 3, 3)
    plt.plot(critic_loss)
    plt.title('Critic Loss')

    plt.show()

### Plot the learned policy - by showing the action probabilities across different state values (1 M)

In [201]:
def plot_learned_policy(actor_model, X_train):
    temp_ranges = np.linspace(min(X_train[:, 0]), max(X_train[:, 0]), num=10)
    action_probs = []

    for temp in temp_ranges:
        state = np.array([temp] + [0] * (X_train.shape[1] - 1))
        probs = actor_model.predict(state.reshape(1, -1))
        action_probs.append(probs[0])

    plt.figure(figsize=(8, 6))
    plt.plot(temp_ranges, np.array(action_probs)[:, 0], label='Decrease')
    plt.plot(temp_ranges, np.array(action_probs)[:, 1], label='Maintain')
    plt.plot(temp_ranges, np.array(action_probs)[:, 2], label='Increase')
    plt.xlabel('Temperature')
    plt.ylabel('Action Probability')
    plt.title('Learned Policy')
    plt.legend()
    plt.show()



In [214]:
file_path = '/content/energydata_complete.csv'
data_df,X_train, X_test, y_train, y_test = load_and_preprocess_data(file_path)
actor_model, critic_model, rewards = train_actor_critic(X_train, y_train,data_df,episodes=2)
#plot_results(rewards, actor_loss=[], critic_loss=[])  # Placeholder for actual loss values
#plot_learned_policy(actor_model, X_train)

test_performance = evaluate_model(actor_model, X_test, y_test,data_df)
print(f"Test Set Performance: {test_performance}")

episode 0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step


<ipython-input-190-cbeae2776644>:22: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if next_index >= len(data):


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
episode 1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step


<ipython-input-190-cbeae2776644>:22: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if next_index >= len(data):


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
i = 0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
max action 2
next_state, reward [ 0.69703373  0.76383698  1.59605521  0.82605785  0.78742746  1.3862594
  0.77387675  0.92888612  0.6546178  -1.75154372 -2.12064782 -0.31110829
 -1.68084536 -1.28421623 -1.72105219 -2.17012709 -1.62119613 -2.96825747
  0.14152171 -1.53231848  0.08929703  0.32375778], Series([], Name: Appliances, dtype: float64)
reward Series([], Name: Appliances, dtype: float64)
i = 1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
max action 2
next_state, reward [ 1.06440038  0.61639264  1.11584352  1.07081602  1.23920233  0.85042519
  1.50059572  1.13337337  1.55303183 -0.44223466  0.05231649 -0.41250654
 -0.25958284 -0.40560424 -0.458305   -0.07004199 -1.03546369 -0.29525857
  0.14152171 -0.22903739 -0.20577779 -0.01621752], Series([], Name: Appliances, dtype: float64)
reward Series([], Name: Appliances, dtype: float64)
i = 2


...

<ipython-input-190-cbeae2776644>:22: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if next_index >= len(data):


next_state, reward [-0.88035977 -0.6604449   0.01418139 -0.69633798 -0.02576732  0.14820325
 -0.05869043  0.11093711  0.26249235 -0.55280971 -0.05416122 -0.29267225
 -0.40009664  0.18998976  0.67356594 -0.56475477  0.1251543   0.10781907
 -1.215052   -0.46744247 -1.31399774  0.79972319], Series([], Name: Appliances, dtype: float64)
reward Series([], Name: Appliances, dtype: float64)
i = 3945
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step


<ipython-input-190-cbeae2776644>:22: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if next_index >= len(data):
<ipython-input-190-cbeae2776644>:22: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if next_index >= len(data):


max action 2
next_state, reward [ 0.81533824  0.93560203  1.47807933  0.56335074  0.78742746  1.57289828
  0.47844968  0.78063286  0.97063452 -0.59301881 -0.53822526 -0.06631858
  0.04678331 -0.92656425 -1.22558444 -0.3574838  -0.21173756 -0.118611
  0.14152171  0.14049047  0.46320864 -1.24012858], Series([], Name: Appliances, dtype: float64)
reward Series([], Name: Appliances, dtype: float64)
i = 3946
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
max action 2
next_state, reward [ 1.25742353  1.17728914  1.26040552  0.43444477  0.56515422  1.13394115
  0.39945849  1.61391841  0.95243461 -0.96997919 -0.78558117 -0.89594062
 -1.15794975 -0.42777275 -0.74616855 -0.99689519 -1.05970969 -0.65497725
  0.14152171 -0.33234626  0.77179834 -0.01621752], Series([], Name: Appliances, dtype: float64)
reward Series([], Name: Appliances, dtype: float64)
Test Set Performance: nan


<ipython-input-190-cbeae2776644>:22: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if next_index >= len(data):
/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/usr/local/lib/python3.10/dist-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)


In [ ]:
data_df

#### Conclusion (0.5 M)

In [ ]:
# Provide an analysis on a comparison of the energy consumption
# before and after applying the reinforcement learning algorithm.